### 40.係り受け解析結果の読み込み（形態素）

In [ ]:
class Morph(object):  # Morphクラスを定義し、形態素の情報を格納するクラス
    def __init__(self, pos):  # クラスの初期化メソッド（コンストラクタ）。posリストから各種形態素情報を抽出して属性に設定
        self.surface = pos[0]  # 表層形（文章に実際に現れる文字列）を設定
        self.base = pos[7]  # 基本形（辞書形）を設定
        self.pos = pos[1]  # 品詞を設定
        self.pos1 = pos[2]  # 品詞の細分類を設定

with open("ai.ja.txt.parsed", "r") as f:  # "ai.ja.txt.parsed"というファイルを読み取りモードで開く
    lines = f.readlines()  # ファイルの全行を読み込み、linesリストに格納
    ai_list = []  # 一時的に形態素を格納するリスト
    morph_list = []  # 文ごとの形態素リストを保存するリスト
    
    for text in lines:  # ファイルの各行に対して処理を実行
        if text[0:3] == "EOS":  # "EOS"で始まる行を検出した場合の処理
            if ai_list:  # ai_listに要素がある場合
                morph_list.append(ai_list)  # morph_listに追加
                ai_list = []  # ai_listをリセット
            continue  # この行の処理をスキップ
        
        if text[0] == "*":  # "*"で始まる行（文節情報）をスキップ
            continue
        
        pos = text.split("\t")  # タブ区切りで行を分割
        temp = pos[1].split(",")  # 品詞情報の詳細を取得（カンマ区切りの追加情報）
        pos.pop()  # 元のpos[1]を削除
        pos.extend(temp)  # tempの追加情報をposに結合
        
        ai_list.append(Morph(pos).__dict__)  # Morphオブジェクトを作成し、その辞書表現をai_listに追加

morph_list  # 最終的な形態素リストを表示

[[{'surface': '人工', 'base': '人工', 'pos': '名詞', 'pos1': '一般'},
  {'surface': '知能', 'base': '知能', 'pos': '名詞', 'pos1': '一般'}],
 [{'surface': '人工', 'base': '人工', 'pos': '名詞', 'pos1': '一般'},
  {'surface': '知能', 'base': '知能', 'pos': '名詞', 'pos1': '一般'},
  {'surface': '（', 'base': '（', 'pos': '記号', 'pos1': '括弧開'},
  {'surface': 'じん', 'base': 'じん', 'pos': '名詞', 'pos1': '一般'},
  {'surface': 'こうち', 'base': 'こうち', 'pos': '名詞', 'pos1': '一般'},
  {'surface': 'のう', 'base': 'のう', 'pos': '助詞', 'pos1': '終助詞'},
  {'surface': '、', 'base': '、', 'pos': '記号', 'pos1': '読点'},
  {'surface': '、', 'base': '、', 'pos': '記号', 'pos1': '読点'},
  {'surface': 'AI', 'base': '*\n', 'pos': '名詞', 'pos1': '一般'},
  {'surface': '〈', 'base': '〈', 'pos': '記号', 'pos1': '括弧開'},
  {'surface': 'エーアイ', 'base': '*\n', 'pos': '名詞', 'pos1': '固有名詞'},
  {'surface': '〉', 'base': '〉', 'pos': '記号', 'pos1': '括弧閉'},
  {'surface': '）', 'base': '）', 'pos': '記号', 'pos1': '括弧閉'},
  {'surface': 'と', 'base': 'と', 'pos': '助詞', 'pos1': '格助詞'},
  {'sur

In [4]:
print(temp)

['記号', '句点', '*', '*', '*', '*', '。', '。', '。\n']


## 41.係り受け解析結果の読み込み
40に加えて，文節を表すクラスChunkを実装せよ．このクラスは形態素（Morphオブジェクト）のリスト（morphs），係り先文節インデックス番号（dst），係り元文節インデックス番号のリスト（srcs）をメンバ変数に持つこととする．さらに，入力テキストの係り受け解析結果を読み込み，１文をChunkオブジェクトのリストとして表現し，冒頭の説明文の文節の文字列と係り先を表示せよ．本章の残りの問題では，ここで作ったプログラムを活用せよ．

In [5]:
class Chunk(object):  # 文節情報を保持するChunkクラスを定義
    def __init__(self, bun, num, chunk_list):  # クラスの初期化メソッド
        self.morphs = bun  # 文節内の形態素（単語）リスト
        self.dst = num  # この文節の係り先インデックス
        self.srcs = chunk_list  # この文節に係る文節のリスト

with open("ai.ja.txt.parsed","r") as f:  # 形態素解析済みファイルを読み取りモード（読み込み専用）で開く
    lines = f.readlines()  # ファイルの全行を読み込む
    all_sentence = []  # 全文のチャンク（文節）情報を格納するリスト
    sentence = []  # 現在処理中の文節内の形態素リスト
    Flag = 0  # EOSを検出したことを示すフラグ
    chunk_dic = {}  # 係り受け関係を保存する辞書（{係り先：[係り元のリスト]}）
    pnum = -2  # 係り先インデックスの初期値（初期化のため-2を使用）
    bnum = -2  # 係り元インデックスの初期値（初期化のため-2を使用）

    for text in lines:  # ファイルの各行を順次処理
        if text[0] == "*":  # 文節情報行の処理
            chunk_dic.setdefault(pnum,[]).append(bnum)  # 係り先辞書に係り元を追加（存在しない場合は空リストを作成）
            if bnum not in chunk_dic:  # 係り元がまだ辞書に存在しない場合
                chunk_dic[bnum] = []  # 空のリストを作成
            if sentence:  # 現在の文節に形態素が存在する場合
                all_sentence.append(Chunk(sentence, pnum, chunk_dic[bnum]).__dict__)  # Chunkオブジェクトを辞書形式で全文リストに追加
            sentence = []  # 現在の文節リストをリセット
            pnum = int(text.split(" ")[2][:-1])  # 係り先インデックスを取得
            bnum = int(text.split(" ")[1])  # 係り元インデックスを取得
            if Flag == 1:  # 前の行がEOSだった場合（新しい文の開始）
                chunk_dic = {}  # 係り受け辞書をリセット
                Flag = 0  # フラグをリセット
                continue

        if text[0:3] == "EOS":  # 文の終わり（End of Sentence）を検出
            Flag = 1  # EOSフラグを立てる
        else:  # 通常の形態素行の処理
            word = text.split("\t")  # タブで行を分割
            sentence.append(word[0])  # 形態素（単語）を現在の文節リストに追加

all_sentence  # 全文の文節情報リストを表示

[{'morphs': ['* 0 -1D 1/1 0.000000\n', '人工', '知能'], 'dst': -1, 'srcs': []},
 {'morphs': ['人工', '知能'], 'dst': 17, 'srcs': []},
 {'morphs': ['* 1 17D 2/3 0.613549\n', '（', 'じん', 'こうち', 'のう', '、', '、'],
  'dst': 17,
  'srcs': []},
 {'morphs': ['* 2 3D 0/0 0.758984\n', 'AI'], 'dst': 3, 'srcs': []},
 {'morphs': ['* 3 17D 1/5 0.517898\n', '〈', 'エーアイ', '〉', '）', 'と', 'は', '、'],
  'dst': 17,
  'srcs': [2]},
 {'morphs': ['* 4 5D 2/2 1.035972\n', '「', '『', '計算'], 'dst': 5, 'srcs': []},
 {'morphs': ['* 5 9D 0/3 1.243687\n', '（', '）', '』', 'という'],
  'dst': 9,
  'srcs': [4]},
 {'morphs': ['* 6 9D 0/1 0.691934\n', '概念', 'と'], 'dst': 9, 'srcs': []},
 {'morphs': ['* 7 8D 1/1 1.048596\n', '『', 'コンピュータ'], 'dst': 8, 'srcs': []},
 {'morphs': ['* 8 9D 0/3 1.540775\n', '（', '）', '』', 'という'],
  'dst': 9,
  'srcs': [7]},
 {'morphs': ['* 9 10D 0/1 2.129047\n', '道具', 'を'],
  'dst': 10,
  'srcs': [5, 6, 8]},
 {'morphs': ['* 10 12D 0/1 1.363632\n', '用い', 'て'], 'dst': 12, 'srcs': [9]},
 {'morphs': ['* 11 12D 1/3 2

## 42. 係り元と係り先の文節の表示
係り元の文節と係り先の文節のテキストをタブ区切り形式ですべて抽出せよ．ただし，句読点などの記号は出力しないようにせよ．

In [6]:
import MeCab  # MeCab形態素解析器をインポート
import unidic  # UniDic辞書をインポート
mecab = MeCab.Tagger("")  # MeCabのTaggerオブジェクトを初期化

text_dic = {}  # 文節のテキストを保存する辞書
i = 0  # 文節のインデックスカウンター
kakari_prelist = []  # 一時的な係り受け関係リスト
kakari_list = []  # 最終的な係り受け関係を格納するリスト

for line in all_sentence:  # 全文節に対して繰り返し処理
    text = ""  # 現在の文節のテキストを初期化
    for sign_check in line["morphs"]:  # 文節内の各形態素に対して
        if mecab.parse(sign_check).split("\t")[1].split(",")[0] in "補助記号":  # 補助記号（句読点など）を除外
            pass  # 何もしない
        else:
            text += sign_check.split("\t")[0]  # 補助記号以外の形態素をテキストに追加
    
    text_dic[i] = text  # 現在の文節のテキストを辞書に保存
    i += 1  # インデックスをインクリメント
    
    if line["srcs"] == []:  # この文節に係る文節がない場合
        pass  # 何もしない
    else:
        pnum = line["srcs"]  # この文節に係る文節のインデックスリスト
        for j in pnum:
            kakari_prelist.append(text_dic[int(j)] + '\t' + text)  # 係り元と係り先のテキストをタブ区切りで一時リストに追加
    
    if line["dst"] == 1:  # この文節が文末（係り先が文末）の場合
        if kakari_prelist:  # 一時係り受けリストが空でない場合
            kakari_list.append(kakari_prelist)  # 係り受けリストを最終リストに追加
            kakari_prelist = []  # 一時リストをリセット
            text_dic = {}  # テキスト辞書をリセット
            i = 0  # インデックスをリセット

kakari_list  # 最終的な係り受け関係リストを表示

[['じんこうちのう\tエーアイとは',
  'エーアイとは\tという',
  '概念と\tという',
  '計算\t道具を',
  'という\t道具を',
  'コンピュータ\t道具を',
  'という\t用いて',
  '道具を\t研究する',
  '用いて\t研究する',
  '知能を\t計算機科学',
  '研究する\tの',
  '計算機科学\t一分野を',
  'の\t指す',
  '人工知能\t語',
  '人工知能\t語',
  'AI\t語',
  '一分野を\t語',
  '語\t推論',
  '言語の\t推論',
  '理解や\t問題解決などの',
  '推論\t知的行動を',
  '問題解決などの\t代わって',
  '知的行動を\t代わって',
  '人間に\t行わせる',
  '代わって\t行わせる',
  'コンピューターに\t技術または',
  '技術または\tコンピュータによる',
  '計算機\t情報処理システムの',
  'コンピュータによる\t情報処理システムの',
  '知的な\t実現に関する',
  '情報処理システムの\t実現に関する',
  '指す\t研究分野とも',
  '行わせる\t研究分野とも',
  '設計や\t研究分野とも',
  '実現に関する\tされる'],
 ['解説で\t解説で',
  '佐藤理史は\t佐藤理史は',
  '情報工学者通信工学者の\t述べている',
  '次のように\t述べている',
  '述べている\t述べている'],
 ['知的能力を\t知的能力を',
  'コンピュータ上で\t実現する',
  '実現する\t実現する',
  '様々な\t技術ソフトウェアコンピュータシステム',
  '技術ソフトウェアコンピュータシステム\t技術ソフトウェアコンピュータシステム',
  '機械翻訳かな漢字変換構文解析等\t機械翻訳かな漢字変換構文解析等',
  '専門家の\t専門家の',
  '推論判断を\t推論判断を',
  '模倣する\t模倣する',
  'エキスパートシステム\tエキスパートシステム',
  '解析して\t解析して',
  'パターンを\tパターンを',
  '特定の\t検出抽出したりする',
  '検出抽出したりする\t検出抽出したりする',
  '画像データを\t画像認識

## 43.名詞を含む文節が動詞を含む文節にかかるものを抽出
名詞を含む文節が、動詞を含む文節に係るとき、これらをタブ区切り形式で抽出せよ、ただし、功徳店などの記号は出力しないようにせよ

多次元の係り受けリストを一次元に平坦化
各係り受け関係について、係り元と係り先の品詞を解析
名詞と動詞の両方が存在する係り受け関係を抽出
抽出した係り受け関係をNV_listに保存

主な特徴：

MeCabを使用して各単語の品詞を判定
フラグを使用して名詞と動詞の存在を追跡
係り受け関係における文法的な関係性を分析

In [7]:
import itertools  # リストの平坦化などに使用するライブラリ

NV_list = []  # 名詞-動詞のペアを保存するリスト
Flag1 = 0  # 名詞の存在を示すフラグ
Flag2 = 0  # 動詞の存在を示すフラグ

kakari_list_flatten = list(itertools.chain.from_iterable(kakari_list))  # 多次元リストを一次元リストに平坦化

for line in kakari_list_flatten:  # 平坦化されたリストの各行に対して処理
    text = line.split('\t')  # タブで係り元と係り先を分割
    pretext = mecab.parse(text[0]).split("\t")  # 係り元の形態素解析結果を取得
    backtext = mecab.parse(text[1]).split("\t")  # 係り先の形態素解析結果を取得

    for ptemp in pretext:  # 係り元の各形態素に対して
        pp = ptemp.split(",")[0]  # 品詞を取得
        if pp == "名詞":  # 名詞が存在する場合
            Flag1 = 1  # フラグを立てる

    for btemp in backtext:  # 係り先の各形態素に対して
        bb = btemp.split(",")[0]  # 品詞を取得
        if bb == "動詞":  # 動詞が存在する場合
            Flag2 = 1  # フラグを立てる

    if Flag1 == 1 and Flag2 == 1:  # 名詞と動詞の両方が存在する場合
        NV_list.append(line)  # 係り受け関係のラインをリストに追加

    Flag1 = 0  # フラグをリセット
    Flag2 = 0  # フラグをリセット

NV_list  # 名詞-動詞のペアリストを表示

['エーアイとは\tという',
 '概念と\tという',
 '道具を\t研究する',
 '問題解決などの\t代わって',
 '知的行動を\t代わって',
 '人間に\t行わせる',
 '技術または\tコンピュータによる',
 '情報処理システムの\t実現に関する',
 '実現に関する\tされる',
 '情報工学者通信工学者の\t述べている',
 '次のように\t述べている',
 'コンピュータ上で\t実現する',
 '実現する\t実現する',
 '模倣する\t模倣する',
 '解析して\t解析して',
 '特定の\t検出抽出したりする',
 '検出抽出したりする\t検出抽出したりする',
 '1956年に\t命名された',
 'ダートマス会議で\t命名された',
 'ジョンマッカーシーにより\t命名された',
 '命名された\t命名された',
 '主体と\tする',
 'アプローチという\tアプローチという',
 '現在では\t使われている',
 '記号処理を\t使われている',
 '模倣した\t模倣した',
 '人工無脳が\t出されるが',
 '引き合いに\t出されるが',
 '人間の\tさせようという',
 '暗黙に\t持つ',
 '計算機に\t困難視されている',
 '人間が\t困難視されている',
 '実用への\t困難視されている',
 '困難視されている\t困難視されている',
 'アプローチとしては\tアプローチとしては',
 'ファジィ理論や\t知られているが',
 '人工知能である\t人工知能である',
 'その後\t集めた',
 'サポートベクターマシンが\t集めた',
 '注目を\t集めた',
 '元に\t行う',
 '学習を\t行う',
 '強化学習という\t強化学習という',
 '宇宙において\t宇宙において',
 '形質である\t形質である',
 'レイカーツワイルという\tレイカーツワイルという',
 '機械的に\t表現し',
 '表現し\t表現し',
 '知性とは\t実装するという',
 '知性を\t実装するという',
 '実装するという\t実装するという',
 '作業である\t作業である',
 '2010年代\t登場により',
 '登場により\t登場により',
 '社会に\t浸透して',
 '浸透して\t浸透して',
 '一過性の\t

## 44.係り受け木の可視化
与えられた文の係り受け木を有向グラフとして可視化せよ．可視化には，Graphviz等を用いるとよい．

In [8]:
import MeCab
import unidic
mecab= MeCab.Tagger("")
text_dic = {}
i = 0
kakari_prelist = []
kakari_list = []
for line in all_sentence:
    text = ""
    for sign_check in line["morphs"]:
        if mecab.parse(sign_check).split("\t")[1].split(",")[0] in "補助記号":#記号の除去
            pass
        else:
            text += sign_check.split("\t")[0]
    #辞書に追加、かかり元を参照する
    text = str(i) + " "+ text #44番かかり受け木作成用に追加
    text_dic[i] = text
    i += 1
    ##出力
    if line["srcs"]==[]:
        pass
    else:
        pnum = line["srcs"]
        for j in pnum:
            kakari_prelist.append(text_dic[int(j)] + '\t' + text)
    if line["dst"]==-1:
        if kakari_prelist:
            kakari_list.append(kakari_prelist)#44番用, #45番用
        kakari_prelist = []
        text_dic = {}
        i = 0
kakari_list

[['2 AI\t3 エーアイとは',
  '4 計算\t5 という',
  '7 コンピュータ\t8 という',
  '5 という\t9 道具を',
  '6 概念と\t9 道具を',
  '8 という\t9 道具を',
  '9 道具を\t10 用いて',
  '10 用いて\t12 研究する',
  '11 知能を\t12 研究する',
  '12 研究する\t13 計算機科学',
  '13 計算機科学\t14 の',
  '14 の\t15 一分野を',
  '15 一分野を\t16 指す',
  '0 人工知能\t17 語',
  '1 じんこうちのう\t17 語',
  '3 エーアイとは\t17 語',
  '16 指す\t17 語',
  '18 言語の\t20 推論',
  '19 理解や\t20 推論',
  '20 推論\t21 問題解決などの',
  '21 問題解決などの\t22 知的行動を',
  '22 知的行動を\t24 代わって',
  '23 人間に\t24 代わって',
  '24 代わって\t26 行わせる',
  '25 コンピューターに\t26 行わせる',
  '26 行わせる\t27 技術または',
  '28 計算機\t29 コンピュータによる',
  '29 コンピュータによる\t31 情報処理システムの',
  '30 知的な\t31 情報処理システムの',
  '31 情報処理システムの\t33 実現に関する',
  '32 設計や\t33 実現に関する',
  '17 語\t34 研究分野とも',
  '27 技術または\t34 研究分野とも',
  '33 実現に関する\t34 研究分野とも',
  '34 研究分野とも\t35 される'],
 ['0 日本大百科全書ニッポニカの\t1 解説で',
  '2 情報工学者通信工学者の\t3 佐藤理史は',
  '1 解説で\t5 述べている',
  '3 佐藤理史は\t5 述べている',
  '4 次のように\t5 述べている'],
 ['0 人間の\t1 知的能力を',
  '1 知的能力を\t3 実現する',
  '2 コンピュータ上で\t3 実現する',
  '3 実現する\t5 技術ソフトウェアコンピュータシステム',
  '4 様々な\t5 技術ソ

In [9]:
!apt install fonts-ipafont-gothic

'apt' �́A�����R�}���h�܂��͊O���R�}���h�A
����\�ȃv���O�����܂��̓o�b�` �t�@�C���Ƃ��ĔF������Ă��܂���B


In [ ]:
from graphviz import Digraph
i = 0
lines = kakari_list[0]

graph = Digraph(format="png")
graph.attr('edge', fontname = 'IPAGothic')
for line in lines:
    text = line.split("\t")
    graph.node(text[0])
    graph.node(text[1])
    graph.edge(text[0], text[1])

graph.attr("node", fontname="Noto Sans JP")
graph.attr("edge", fontname="Noto Sans JP")
graph.render("output{}".format(str(i).zfill(3)))

'output000.png'

## 45. 動詞の格パターンの抽出
今回用いている文章をコーパスと見なし，日本語の述語が取りうる格を調査したい． 動詞を述語，動詞に係っている文節の助詞を格と考え，述語と格をタブ区切り形式で出力せよ． ただし，出力は以下の仕様を満たすようにせよ．
動詞を含む文節において，最左の動詞の基本形を述語とする
述語に係る助詞を格とする
述語に係る助詞（文節）が複数あるときは，すべての助詞をスペース区切りで辞書順に並べる
「ジョン・マッカーシーはAIに関する最初の会議で人工知能という用語を作り出した。」という例文を考える． この文は「作り出す」という１つの動詞を含み，「作り出す」に係る文節は「ジョン・マッカーシーは」，「会議で」，「用語を」であると解析された場合は，次のような出力になるはずである．

作り出す	で は を
このプログラムの出力をファイルに保存し，以下の事項をUNIXコマンドを用いて確認せよ．

コーパス中で頻出する述語と格パターンの組み合わせ
「行う」「なる」「与える」という動詞の格パターン（コーパス中で出現頻度の高い順に並べよ）

In [ ]:
import MeCab  # MeCab形態素解析器をインポート
import unidic  # UniDic辞書をインポート
mecab = MeCab.Tagger("")  # MeCabのTaggerオブジェクトを初期化

text_dic = {}  # 文節のテキストを保存する辞書
i = 0  # 文節のインデックスカウンター
kakari_prelist = []  # 一時的な係り受け関係リスト
kakari_list = []  # 最終的な係り受け関係を格納するリスト

for line in all_sentense:  # 全文節に対して繰り返し処理
    text = ""  # 現在の文節のテキストを初期化
    for sign_check in line["morphs"]:  # 文節内の各形態素に対して
        if mecab.parse(sign_check).split("\t")[1].split(",")[0] in "補助記号":  # 補助記号（句読点など）を除外
            pass  # 何もしない
        else:
            text += sign_check.split("\t")[0]  # 補助記号以外の形態素をテキストに追加
    
    text = str(i) + " " + text  # 44番かかり受け木作成用にインデックスを追加
    text_dic[i] = text  # 現在の文節のテキストを辞書に保存
    i += 1  # インデックスをインクリメント
    
    if line["srcs"] == []:  # この文節に係る文節がない場合
        pass  # 何もしない
    else:
        pnum = line["srcs"]  # この文節に係る文節のインデックスリスト
        for j in pnum:
            kakari_prelist.append(text_dic[int(j)] + '\t' + text)  # 係り元と係り先のテキストをタブ区切りで一時リストに追加
    
    if line["dst"] == -1:  # この文節が文末（係り先が-1）の場合
        if kakari_prelist:  # 一時係り受けリストが空でない場合
            kakari_list.append(kakari_prelist)  # 係り受けリストを最終リストに追加
        kakari_prelist = []  # 一時リストをリセット
        text_dic = {}  # テキスト辞書をリセット
        i = 0  # インデックスをリセット

kakari_list  # 最終的な係り受け関係リストを表示

[['2 AI\t3 エーアイとは',
  '4 計算\t5 という',
  '7 コンピュータ\t8 という',
  '5 という\t9 道具を',
  '6 概念と\t9 道具を',
  '8 という\t9 道具を',
  '9 道具を\t10 用いて',
  '10 用いて\t12 研究する',
  '11 知能を\t12 研究する',
  '12 研究する\t13 計算機科学',
  '13 計算機科学\t14 の',
  '14 の\t15 一分野を',
  '15 一分野を\t16 指す',
  '0 人工知能\t17 語',
  '1 じんこうちのう\t17 語',
  '3 エーアイとは\t17 語',
  '16 指す\t17 語',
  '18 言語の\t20 推論',
  '19 理解や\t20 推論',
  '20 推論\t21 問題解決などの',
  '21 問題解決などの\t22 知的行動を',
  '22 知的行動を\t24 代わって',
  '23 人間に\t24 代わって',
  '24 代わって\t26 行わせる',
  '25 コンピューターに\t26 行わせる',
  '26 行わせる\t27 技術または',
  '28 計算機\t29 コンピュータによる',
  '29 コンピュータによる\t31 情報処理システムの',
  '30 知的な\t31 情報処理システムの',
  '31 情報処理システムの\t33 実現に関する',
  '32 設計や\t33 実現に関する',
  '17 語\t34 研究分野とも',
  '27 技術または\t34 研究分野とも',
  '33 実現に関する\t34 研究分野とも',
  '34 研究分野とも\t35 される'],
 ['0 日本大百科全書ニッポニカの\t1 解説で',
  '2 情報工学者通信工学者の\t3 佐藤理史は',
  '1 解説で\t5 述べている',
  '3 佐藤理史は\t5 述べている',
  '4 次のように\t5 述べている'],
 ['0 人間の\t1 知的能力を',
  '1 知的能力を\t3 実現する',
  '2 コンピュータ上で\t3 実現する',
  '3 実現する\t5 技術ソフトウェアコンピュータシステム',
  '4 様々な\t5 技術ソ

In [59]:
import MeCab  # MeCab形態素解析器をインポート
import re  # 正規表現モジュールをインポート
mecab = MeCab.Tagger("")  # MeCabのTaggerオブジェクトを初期化

f = open("verb_pattern.txt", "a")  # 追記モードでファイルをオープン

for lines in kakari_list:  # 係り受けリスト（2次元リスト）の各文に対して
    Flag = 0  # 動詞フラグの初期化
    joshi_dic = {}  # 助詞を保存する辞書
    for text in lines:  # 文中の各係り受け関係に対して
        word = text.split("\t")  # タブで係り元と係り先を分割
        # 係り先（後半）の形態素解析
        word2nd = mecab.parse(word[1].split(" ")[1]).split("\n")
        for item in word2nd:  # 係り先の各形態素に対して
            verb = re.split("[\t,]", item)  # タブとカンマで形態素情報を分割
            if verb[0] == "EOS" or len(verb) == 1:  # EOSや空白行は除外
                continue
            if verb[1] == "動詞":  # 係り先に動詞が含まれる場合
                if Flag == 1:  # 最左動詞のみ処理（「述べて+いる」→「述べる」のみ）
                    continue
                Flag = 1  # 動詞フラグを立てる
                # 係り元（前半）の形態素解析
                word1st = mecab.parse(word[0].split(" ")[1]).split("\n")
                for item2 in word1st:  # 係り元の各形態素に対して
                    joshi = re.split("[\t,]", item2)  # タブとカンマで形態素情報を分割
                    if joshi[0] == "EOS" or len(joshi) == 1:  # EOSや空白行は除外
                        continue
                    if joshi[1] == "助詞":  # 助詞を見つけた場合
                        # 動詞の基本形と助詞を辞書に保存
                        key_verb = word[1].split(" ")[0] + ":" + verb[11]
                        joshi_dic.setdefault(key_verb, []).append(joshi[0])
        Flag = 0  # 動詞フラグをリセット
        i += 1  # インデックスをインクリメント（注意: iが未定義の可能性あり）
    # 辞書の内容をファイルに書き込み
    for k, v in joshi_dic.items():
        k = k.split(":")[1]  # 動詞の基本形を取得
        v = sorted(v)  # 助詞をアルファベット順にソート
        text = str(k) + "\t" + " ".join(v) + "\n"  # タブ区切りのテキストを作成
        f.write(text)  # ファイルに書き込み

f.close()  # ファイルを閉じる

In [60]:
from collections import Counter  # 要素の出現回数をカウントするためのモジュールをインポート

# ファイルを読み込み、重複を数える
with open('verb_pattern.txt', 'r', encoding='utf-8') as f:  # UTF-8エンコーディングでファイルを読み取りモードで開く
    lines = f.readlines()  # ファイルの全行を読み込み、リストとして格納

# 重複をカウントしてソート
counts = Counter(line.strip() for line in lines)  # 各行の前後の空白を削除し、出現回数をカウント
sorted_counts = sorted(counts.items(), key=lambda x: x[1], reverse=True)  # カウント数の降順でソート
    # key=lambda x: x[1]  → 各要素のカウント（2番目の要素）でソート
    # reverse=True  → 降順（多い順）にソート

# 結果を表示
for item, count in sorted_counts:  # ソートされたカウントのリストを反復処理
    print(f"{count} {item}")  # 出現回数と項目を表示

108 する	を
40 する	が
28 する	と
24 する	は を
24 する	に
22 する	で を
18 ある	の
16 よる	の
14 おく	の
12 呼ぶ	と
12 基づく	に
12 する	が に
12 する	の
10 する	て を
10 する	て と
10 行う	を
10 する	に を
10 する	が を
10 する	と は
8 用いる	を
8 する	と を
8 する	て に
8 ある	は
8 する	に は を
8 関わる	に も
8 使う	を
6 超える	を
6 行く	を
6 する	は
6 する	て
6 する	が で
6 受ける	を
6 する	で に
6 する	で
6 いう	と
6 持つ	を
6 つく	の
6 述べる	と
4 する	で に に
4 よる	と の
4 かける	から
4 する	て に を
4 ある	が
4 上回る	で を
4 する	て と は を
4 する	て て と に
4 する	が が
4 含む	に は も
4 至る	に
4 入る	に
4 する	て で
4 持つ	が を
4 する	から を
4 する	が で を
4 扱う	を
4 導き出す	を
4 集める	を
4 する	が て と
4 語る	を
4 いう	や
2 指す	を
2 代わる	に を
2 行う	て に
2 関する	の や
2 述べる	で の は
2 いう	で の
2 使う	で で は も
2 呼ぶ	も
2 いう	に
2 出す	が に
2 いう	に を
2 持つ	が に
2 する	が が は
2 する	の へ
2 知る	て と は も
2 集める	が を
2 行う	に を を
2 ある	と は
2 行く	て に
2 破る	も
2 する	が て と に
2 なる	で と など は
2 呼ぶ	と は
2 繰り返す	を
2 作る	を
2 なす	も
2 通す	や
2 する	て て で に は を を を
2 出す	を
2 行う	が て で は
2 する	て て で で は
2 だす	が で を
2 加える	に
2 見せる	て て て に は を
2 広がる	が に は
2 始まる	て て も
2 なる	が が て て と
2 する	が と
2 行く	は を
2 もたらす	に は を
2 題する	と
2 築く	を
2 出る	が て と に
2 作り出す	で は を
2 しゃべる	は
2 行う

In [51]:
!cat "verb_pattern.txt" | sort | uniq -c | sort -nr | iconv -f UTF-8

'cat' �́A�����R�}���h�܂��͊O���R�}���h�A
����\�ȃv���O�����܂��̓o�b�` �t�@�C���Ƃ��ĔF������Ă��܂���B


##  46.動詞の格フレーム情報の抽出
45のプログラムを改変し，述語と格パターンに続けて項（述語に係っている文節そのもの）をタブ区切り形式で出力せよ．45の仕様に加えて，以下の仕様を満たすようにせよ．

項は述語に係っている文節の単語列とする（末尾の助詞を取り除く必要はない）
述語に係る文節が複数あるときは，助詞と同一の基準・順序でスペース区切りで並べる
「ジョン・マッカーシーはAIに関する最初の会議で人工知能という用語を作り出した。」という例文を考える． この文は「作り出す」という１つの動詞を含み，「作り出す」に係る文節は「ジョン・マッカーシーは」，「会議で」，「用語を」であると解析された場合は，次のような出力になるはずである．

In [61]:
import MeCab  # 日本語形態素解析ライブラリをインポート
import re    # 正規表現モジュールをインポート

mecab = MeCab.Tagger("")  # MeCabのタガーを初期化

frame_list = []  # 最終的な結果を格納するリストを初期化

for lines in kakari_list:  # kakari_listの各行セットを繰り返し処理
    joshi_dic = {}  # 助詞と動詞を格納する辞書を初期化
    Flag = 0  # 動詞処理を追跡するフラグを初期化

    for text in lines:  # 現在の行の各テキストを繰り返し処理
        word = text.split("\t")  # テキストをタブで分割してコンポーネントを分離

        # MeCabを使用して2番目の単語を形態素解析
        word2nd = mecab.parse(word[1].split(" ")[1]).split("\n")

        for item in word2nd:  # 形態素解析結果を繰り返し処理
            verb = re.split("[\t,]", item)  # 形態素情報をタブとカンマで分割

            # 文の末尾または無効なアイテムをスキップ
            if verb[0] == "EOS" or len(verb) == 1:
                continue

            if verb[1] == "動詞":  # アイテムが動詞かどうかを確認
                if Flag == 1:  # すでに動詞が処理されている場合はスキップ
                    continue
                Flag = 1  # フラグを立てて動詞処理中であることを示す

                # 最初の単語（おそらく助詞を含む単語）を解析
                word1st = mecab.parse(word[0].split(" ")[1]).split("\n")

                for item2 in word1st:  # 最初の単語の形態素解析を繰り返し処理
                    joshi = re.split("[\t,]", item2)  # 形態素情報を分割

                    # 文の末尾または無効なアイテムをスキップ
                    if joshi[0] == "EOS" or len(joshi) == 1:
                        continue

                    if joshi[1] == "助詞":  # アイテムが助詞かどうかを確認
                        # 動詞とその基本形を組み合わせたキーを作成
                        key_verb = word[1].split(" ")[0] + ":" + verb[11]
                        
                        # 助詞とその対応する単語を辞書に格納
                        joshi_dic.setdefault(key_verb, []).append([joshi[0], word[0].split(" ")[1]])

        Flag = 0  # 処理後にフラグをリセット

    # 収集された助詞-動詞情報を処理
    for k, v in joshi_dic.items():
        k = k.split(":")[1]  # キーから基本形を抽出
        v = sorted(v, key=lambda x:x[0])  # 助詞でソート
        text1 = []  # 助詞のリスト
        text2 = []  # 対応する単語のリスト

        for v2 in v:
            text1.append(v2[0])  # 助詞を追加
            text2.append(v2[1])  # 単語を追加

        # 形式を整えて最終リストに追加
        temp = str(k) + "\t" + " ".join(text1) + "\t" + " ".join(text2)
        frame_list.append(temp)

frame_list  # 最終結果を返す

['用いる\tを\t道具を',
 'する\tて を\t用いて 知能を',
 '指す\tを\t一分野を',
 '代わる\tに を\t人間に 知的行動を',
 '行う\tて に\t代わって コンピューターに',
 '関する\tの や\t情報処理システムの 設計や',
 '述べる\tで の は\t解説で 次のように 佐藤理史は',
 'する\tで を\tコンピュータ上で 知的能力を',
 'する\tを\t推論判断を',
 'する\tを\t画像データを',
 'する\tて を\t解析して パターンを',
 'する\tで に に\tダートマス会議で 1956年に ジョンマッカーシーにより',
 '用いる\tを\t記号処理を',
 'する\tと を\t主体と 記述を',
 'いう\tで の\t研究での 研究での',
 '使う\tで で は も\t現在では 意味あいでも 現在では 意味あいでも',
 '呼ぶ\tも\t思考ルーチンも',
 'いう\tに\tプログラミング言語による',
 'する\tを\tカウンセラーを',
 '出す\tが に\t人工無脳が 引き合いに',
 'いう\tに を\t計算機に 役割を',
 '呼ぶ\tと\tエキスパートシステムと',
 '持つ\tが に\t人間が 暗黙に',
 'する\tが が は\t出されるが 利用が 実現は',
 'する\tの へ\t実現への 実現への',
 '知る\tて と は も\tアプローチとしては アプローチとしては アプローチとしては アプローチも',
 'ある\tの\t従来の',
 '集める\tが を\tサポートベクターマシンが 注目を',
 '行う\tに を を\t元に 経験を 学習を',
 'ある\tと は\t知性とは 知性とは',
 'する\tを\t知性を',
 'する\tて に\t宇宙において 宇宙において',
 'ある\tは\tことは',
 'よる\tと の\t登場と ビッグデータの',
 '超える\tを\t流行を',
 'する\tて に\t超えて 社会に',
 '行く\tて に\t浸透して 登場により',
 'かける\tから\t2016年から',
 'する\tて に を\t2017年にかけて 2017年にかけて ディープラーニングを',
 'ある\tが\tAIが',
 '破る\tも\tプレイヤーも',
 'する\

## 47.機能動詞構文のマイニング
動詞のヲ格にサ変接続名詞が入っている場合のみに着目したい．46のプログラムを以下の仕様を満たすように改変せよ．

「サ変接続名詞+を（助詞）」で構成される文節が動詞に係る場合のみを対象とする
述語は「サ変接続名詞+を+動詞の基本形」とし，文節中に複数の動詞があるときは，最左の動詞を用いる
述語に係る助詞（文節）が複数あるときは，すべての助詞をスペース区切りで辞書順に並べる
述語に係る文節が複数ある場合は，すべての項をスペース区切りで並べる（助詞の並び順と揃えよ）
例えば「また、自らの経験を元に学習を行う強化学習という手法もある。」という文から，以下の出力が得られるはずである．

学習を行う	に を	元に 経験を

In [53]:
#47
import MeCab
import re
import copy
mecab= MeCab.Tagger("")
result47 = []

for line in frame_list:#46のframelistを使用
    base_verb = line.split("\t")[0]#元の動詞
    joshi_list = line.split("\t")[1].split(" ")#助詞
    verbs_list = line.split("\t")[2].split(" ")#述語になり得る部分
    for verbs, joshi in zip(verbs_list, joshi_list):
        joshi_list_temp = copy.copy(joshi_list)#述語になる名詞は除かれるのでコピーをとっておく
        verbs_list_temp = copy.copy(verbs_list)
        verbs_m = mecab.parse(verbs)#mecabに食わせる
        verbs_m =re.split("[\t,]", verbs_m)#リストの整形
        if verbs_m[0] == "EOS" or len(verbs_m) == 1:
            continue
        if verbs_m[3]=="サ変可能":#サ変を見つける
            if joshi == "を":#をの判定
                verb_result = verbs_m[0]+ joshi + base_verb#出力用の文字列
                joshi_list_temp.remove("を")#述語になったので除去する
                verbs_list_temp.remove(verbs)#同上
                if len(verbs_list_temp)==0:#もし述語になったせいでかかる名詞がなくなったらそれは無くす
                    continue
                #書き出し
                result47.append(verb_result+"\t" + " ".join(joshi_list_temp)+"\t"+" ".join(verbs_list_temp))
            else:
                pass
result47

['記述をする\tと\t主体と',
 '注目を集める\tが\tサポートベクターマシンが',
 '経験を行う\tに を\t元に 学習を',
 '学習を行う\tに を\t元に 経験を',
 '推論をする\tて て で に は を を\tなされている 生成規則を通して ACTRでは 元に ACTRでは 統計的学習を 生成規則を通して',
 '統計をする\tて て で に は を を\tなされている 生成規則を通して ACTRでは 元に ACTRでは 推論ルールを 生成規則を通して',
 '生成をする\tて て で に は を を\tなされている ACTRでは 元に ACTRでは 推論ルールを 統計的学習を 生成規則を通して',
 '進化を見せる\tて て て に は\t活躍している 加えて 生成技術において 生成技術において 敵対的生成ネットワークは',
 '開発を行く\tは\tエイダ・ラブレスは',
 'プログラミングをする\tは\t彼はまた',
 'チューをする\tて と は\t方法として 方法として アランチューリングは',
 'プログラミングをする\tは\tアランカルメラウアーは',
 '投資を上回る\tが\tコストが',
 '意味をする\tから て に\tここから 非構造化データに対して 非構造化データに対して',
 '意味をする\tに\tデータに',
 '研究を進める\tて\t費やして',
 '命令をする\tで\t機構で',
 '運転をする\tに\t元に',
 '運転をする\tて\t基づいて',
 '注目を集める\tから は\tことから ファジィは',
 '制御をする\tから\t少なさから',
 '研究を続ける\tが て\tジェフホーキンスが 向けて',
 '行動を用いる\tて は は\t登場している これは ものではなく',
 '圧倒を付ける\tで に\t画像処理コンテストで 手法に',
 '投資を行く\tで\t民間企業主導で',
 '探索を行う\tで\t無報酬で',
 '推論をする\tて\t経て',
 '共同を始める\tと は も\tマックスプランク研究所とも Googleは マックスプランク研究所とも',
 '研究を行く\tて\t始めており',
 '研究をする\tで で は\t中国では 官民一体で 中国では',
 '研究をする\tで\t日本で',
 '投

## 48. 名詞から根へのパスの抽出
文中のすべての名詞を含む文節に対し，その文節から構文木の根に至るパスを抽出せよ． ただし，構文木上のパスは以下の仕様を満たすものとする．

・各文節は（表層形の）形態素列で表現する
・パスの開始文節から終了文節に至るまで，各文節の表現を” -> “で連結する
「ジョン・マッカーシーはAIに関する最初の会議で人工知能という用語を作り出した。」という例文を考える． CaboChaを係り受け解析に用いた場合，次のような出力が得られると思われる．

ジョンマッカーシーは -> 作り出した
AIに関する -> 最初の -> 会議で -> 作り出した
最初の -> 会議で -> 作り出した
会議で -> 作り出した
人工知能という -> 用語を -> 作り出した
用語を -> 作り出した
KNPを係り受け解析に用いた場合，次のような出力が得られると思われる．


ジョンマッカーシーは -> 作り出した
ＡＩに -> 関する -> 会議で -> 作り出した
会議で -> 作り出した
人工知能と -> いう -> 用語を -> 作り出した
用語を -> 作り出した

In [62]:
#48
# 'ai.ja.txt.parsed'ファイルを読み込み
with open('ai.ja.txt.parsed', "r") as f:
    lines = f.readlines()  # ファイルの全行を読み取る
    text_dic = {}  # テキスト情報を格納する辞書
    dic_list = []  # 辞書のリスト
    text = ""  # 現在処理中のテキスト
    Flag_N = 0  # 名詞フラグ
    Flag_lastline = 0  # 最終行フラグ
    index_num = 0  # インデックス番号

    # 各行を処理
    for line in lines:
        if line == "EOS\n":  # 文章の終わり
            if Flag_lastline == 1:
                if Flag_N == 1:
                    text = "N:"+ text  # 名詞の場合、接頭辞を追加
                    Flag_N = 0
                text_dic[index_num] = [text, num]  # テキスト情報を辞書に保存
                dic_list.append(text_dic)  # 辞書リストに追加
                text_dic = {}  # 辞書をリセット
                Flag_lastline = 0
            continue

        if line[0] == "*":  # 構文解析情報の行
            if Flag_N == 1:
                text = "N:"+ text  # 名詞の場合、接頭辞を追加
                Flag_N = 0
            if int(line.split(" ")[1]) != 0:
                text_dic[index_num] = [text, num]  # テキスト情報を辞書に保存
            num = int(line.split(" ")[2][:-1])  # かかり先
            index_num = int(line.split(" ")[1])  # かかり元
            text = ""  # テキストをリセット
            if num == -1:
                Flag_lastline = 1  # 最終行フラグを設定
            continue

        if line.split("\t")[1][0:2] == "記号":  # 記号をスキップ
            continue

        text += line.split("\t")[0]  # テキストに単語を追加
        if line.split("\t")[1].split(",")[0] == "名詞":  # 名詞の場合
            Flag_N = 1  # 名詞フラグを立てる

def MakeTree(dic_list):  # かかり結びの木を作成
    result = []
    for text in dic_list.items():
        if text[1][0].split(":")[0] == "N":  # 名詞から始まる文節の場合
            temp = ""
            num = int(text[0])
            while True:
                word = dic_list[num][0]  # 現在の単語
                num = int(dic_list[num][1])  # 次の単語のインデックス
                if num == -1:
                    temp += word
                    temp = temp.replace("N:","")  # 名詞の接頭辞を削除
                    break
                else:
                    temp += word + "->"  # 単語間を->で接続
            result.append(temp)
    return result

result_list48 = []
for index_dic in dic_list:
    index = MakeTree(index_dic)  # 各辞書についてツリーを作成
    if len(index) == 0:
        continue
    result_list48.extend(index)  # 結果のリストに追加

result_list48  # 最終結果を返す

['人工知能',
 '人工知能->語->研究分野とも->される',
 'じんこうちのう->語->研究分野とも->される',
 'AI->エーアイとは->語->研究分野とも->される',
 'エーアイとは->語->研究分野とも->される',
 '計算->という->道具を->用いて->研究する->計算機科学->の->一分野を->指す->語->研究分野とも->される',
 '概念と->道具を->用いて->研究する->計算機科学->の->一分野を->指す->語->研究分野とも->される',
 'コンピュータ->という->道具を->用いて->研究する->計算機科学->の->一分野を->指す->語->研究分野とも->される',
 '道具を->用いて->研究する->計算機科学->の->一分野を->指す->語->研究分野とも->される',
 '知能を->研究する->計算機科学->の->一分野を->指す->語->研究分野とも->される',
 '研究する->計算機科学->の->一分野を->指す->語->研究分野とも->される',
 '計算機科学->の->一分野を->指す->語->研究分野とも->される',
 '一分野を->指す->語->研究分野とも->される',
 '語->研究分野とも->される',
 '言語の->推論->問題解決などの->知的行動を->代わって->行わせる->技術または->研究分野とも->される',
 '理解や->推論->問題解決などの->知的行動を->代わって->行わせる->技術または->研究分野とも->される',
 '推論->問題解決などの->知的行動を->代わって->行わせる->技術または->研究分野とも->される',
 '問題解決などの->知的行動を->代わって->行わせる->技術または->研究分野とも->される',
 '知的行動を->代わって->行わせる->技術または->研究分野とも->される',
 '人間に->代わって->行わせる->技術または->研究分野とも->される',
 'コンピューターに->行わせる->技術または->研究分野とも->される',
 '技術または->研究分野とも->される',
 '計算機->コンピュータによる->情報処理システムの->実現に関する->研究分野とも->される',
 'コンピュータによる->情報処理システムの->実現に関する

## 49. 名詞間の係り受けパスの抽出
文中のすべての名詞句のペアを結ぶ最短係り受けパスを抽出せよ．ただし，名詞句ペアの文節番号がiとj（i<j）のとき，係り受けパスは以下の仕様を満たすものとする．

・問題48と同様に，パスは開始文節から終了文節に至るまでの各文節の表現（表層形の形態素列）を” -> “で連結して表現する
・文節iとjに含まれる名詞句はそれぞれ，XとYに置換する
また，係り受けパスの形状は，以下の2通りが考えられる．
・文節iから構文木の根に至る経路上に文節jが存在する場合:
文節iから文節jのパスを表示
・上記以外で，文節iと文節jから構文木の根に至る経路上で共通の文節kで交わる場合: 文節iから文節kに至る直前のパスと文節jから文節kに至る直前までのパス，文節kの内容を” | “で連結して表示
「ジョン・マッカーシーはAIに関する最初の会議で人工知能という用語を作り出した。」という例文を考える． CaboChaを係り受け解析に用いた場合，次のような出力が得られると思われる．

Xは | Yに関する -> 最初の -> 会議で | 作り出した
Xは | Yの -> 会議で | 作り出した
Xは | Yで | 作り出した
Xは | Yという -> 用語を | 作り出した
Xは | Yを | 作り出した
Xに関する -> Yの
Xに関する -> 最初の -> Yで
Xに関する -> 最初の -> 会議で | Yという -> 用語を | 作り出した
Xに関する -> 最初の -> 会議で | Yを | 作り出した
Xの -> Yで
Xの -> 会議で | Yという -> 用語を | 作り出した
Xの -> 会議で | Yを | 作り出した
Xで | Yという -> 用語を | 作り出した
Xで | Yを | 作り出した
Xという -> Yを
KNPを係り受け解析に用いた場合，次のような出力が得られると思われる．


Xは | Yに -> 関する -> 会議で | 作り出した。
Xは | Yで | 作り出した。
Xは | Yと -> いう -> 用語を | 作り出した。
Xは | Yを | 作り出した。
Xに -> 関する -> Yで
Xに -> 関する -> 会議で | Yと -> いう -> 用語を | 作り出した。
Xに -> 関する -> 会議で | Yを | 作り出した。
Xで | Yと -> いう -> 用語を | 作り出した。
Xで | Yを | 作り出した。
Xと -> いう -> Yを

In [63]:
import itertools  # 全ての組み合わせを生成するためのモジュールをインポート
import MeCab  # 日本語形態素解析ライブラリをインポート
mecab = MeCab.Tagger("")  # MeCabタガーを初期化
result_list49 = []  # 最終結果を格納するリストを初期化

def XYEncoder(text, z):  # 名詞をXまたはYに置き換える関数
    # textを形態素解析し、zで指定された文字（XまたはY）に名詞を置き換える
    mtext = mecab.parse(text)  # テキストを形態素解析
    result = ""
    Flag = 0
    mtext = mtext.split("\n")
    temp = []
    for m in mtext:
        if m.split("\t")[0] == "EOS" or len(m) == 0:  # 文の終わりや空行をスキップ
            continue
        hinshi = m.split("\t")[1].split(",")[0]  # 品詞を取得
        temp.append(hinshi)
        # 名詞、形状詞、代名詞以外の単語はそのまま、名詞は指定された文字に置き換え
        if hinshi!="名詞" and hinshi!="形状詞" and hinshi!="代名詞":
            result += m.split("\t")[0]
        elif Flag == 1:
            continue
        else:
            result += z
            Flag = 1
    return result

def Clener(text):  # 単語のIDを削除する関数
    for i in range(len(text)):
        text[i] = text[i].split(":")[0]  # ":"以降を削除
    return text

def Remakedict(predic):  # 各単語にユニークなIDを付与する関数
    numembid = 0
    for n, text in predic.items():
        temp = [text[0] + ":{}".format(str(numembid)), text[1]]  # IDを追加
        predic[n] = temp
        numembid += 1
    return predic

def Pairmaker(predic, sent_list):  # 名詞の組み合わせと係り受け木を抽出する関数
    n_list = []  # 名詞のインデックスを格納するリスト
    kakari_dic = {}  # 係り受け木を格納する辞書
    i = 0
    for n, text in predic.items():
        if text[0].split(":")[0] == "N":  # 名詞で始まる文節のみ処理
            n_list.append(n)
            kakari_dic[n] = sent_list[i]
            i += 1
    return n_list, kakari_dic

# 問題48で作成したdic_listの各文に対して処理
for predic in dic_list:
    result_list = []
    predic = Remakedict(predic)  # 単語にIDを付与
    sent_list = MakeTree(predic)  # 係り受け木を作成
    n_list, kakari_dic = Pairmaker(predic, sent_list)  # 名詞の組み合わせと係り受け木を抽出
    conb_list = list(itertools.combinations(n_list, 2))  # 名詞の全組み合わせを生成

    for conb in conb_list:  # 各名詞の組み合わせに対して処理
        sent1 = kakari_dic[conb[0]].split("->")  # 最初の係り受け木
        sent2 = kakari_dic[conb[1]].split("->")  # 2番目の係り受け木
        break_Flag = 0
        
        for sen2 in reversed(sent2):  # 後ろから共通の単語を探索
            for sen1 in reversed(sent1):
                if sen2 == sen1:  # 共通の単語を見つけた場合の処理
                    last_word = sen2
                    sent1 = sent1[:-1]
                    sent2 = sent2[:-1]
                    if len(sent2) == 0:
                        sent1.append(last_word)
                        break_Flag = 2
                        break
                    elif len(sent2) == 1:
                        if len(sent1) == 1:
                            break_Flag = 1
                        else:
                            sent1[len(sent1)-1] = sent2[0]
                            break_Flag = 2
                        break
                    else:
                        sen2 = sent2[len(sent2)-1]
                else:
                    break_Flag = 1
                    break
            
            # 結果の生成
            if break_Flag == 1:
                sent1[0] = XYEncoder(sent1[0], "X")  # 最初の単語をXに置き換え
                sent2[0] = XYEncoder(sent2[0], "Y")  # 最初の単語をYに置き換え
                sent1 = Clener(sent1)  # IDを削除
                sent2 = Clener(sent2)
                last_word = last_word.split(":")[0]
                result49 = "->".join(sent1) + "|" + "->".join(sent2) + "|" + last_word
                break_Flag = 0
                break
            elif break_Flag == 2:
                sent1[0] = XYEncoder(sent1[0], "X")  # 最初の単語をXに置き換え
                sent1[-1] = XYEncoder(sent1[-1], "Y")  # 最後の単語をYに置き換え
                sent1 = Clener(sent1)  # IDを削除
                result49 = "->".join(sent1)
                break_Flag = 0
                break

        # 結果のフィルタリング
        if "X" not in result49 or "Y" not in result49:
            pass
        else:
            result_list.append(result49)  # 結果を一時リストに追加

    if len(result_list) == 0:  # 空の結果リストはスキップ
        continue
    result_list49.append(result_list)  # 最終結果リストに追加

result_list49  # 最終結果を返す

[['X|Yのう|語',
  'X|Y->エーアイとは|語',
  'X|Yとは|語',
  'X|Y->という->道具を->用いて->研究する->計算機科学->の->一分野を->指す|語',
  'X|Yと->道具を->用いて->研究する->計算機科学->の->一分野を->指す|語',
  'X|Y->という->道具を->用いて->研究する->計算機科学->の->一分野を->指す|語',
  'X|Yを->用いて->研究する->計算機科学->の->一分野を->指す|語',
  'X|Yを->研究する->計算機科学->の->一分野を->指す|語',
  'X|Yする->計算機科学->の->一分野を->指す|語',
  'X|Y->の->一分野を->指す|語',
  'X|Yを->指す|語',
  'X->Y',
  'X->語|Yの->推論->問題解決などの->知的行動を->代わって->行わせる->技術または|研究分野とも',
  'X->語|Yや->推論->問題解決などの->知的行動を->代わって->行わせる->技術または|研究分野とも',
  'X->語|Y->問題解決などの->知的行動を->代わって->行わせる->技術または|研究分野とも',
  'X->語|Yなどの->知的行動を->代わって->行わせる->技術または|研究分野とも',
  'X->語|Yを->代わって->行わせる->技術または|研究分野とも',
  'X->語|Yに->代わって->行わせる->技術または|研究分野とも',
  'X->語|Yに->行わせる->技術または|研究分野とも',
  'X->Yまたは',
  'X->語|Y->コンピュータによる->情報処理システムの->実現に関する|研究分野とも',
  'X->語|Yによる->情報処理システムの->実現に関する|研究分野とも',
  'X->語|Yな->情報処理システムの->実現に関する|研究分野とも',
  'X->語|Yの->実現に関する|研究分野とも',
  'X->語|Yや->実現に関する|研究分野とも',
  'X->Yに関する',
  'X->語->Yとも',
  'Xのう|Y->エーアイとは|語',
  'Xのう|Yとは|語',
  'Xのう|Y->という->道具を->用いて->研究する->計算機科学->の->一分野を